In [9]:
import numpy as np
import pandas as pd
import plotly.express as px
from scipy.stats import qmc
from os import path
from self_driving_lab_demo.utils.plotting import plot_and_save

In [10]:
bounds = {"x1": [0, 1], "x2": [0, 1]}
num_samples = 10

## Uninformed Sampling Methods

I.e. sampling methods that do not incorporate information about the objective function
to be optimized.

### Grid Samples

In [11]:
from sklearn.model_selection import ParameterGrid

def get_grid_samples(bounds, num_samples = 10, seed=None):
    # seed is unused, for compatibility only
    param_grid = {}
    num_pts_per_dim = max(1, np.floor(num_samples ** (1 / len(bounds))).astype(int))
    for name, bnd in bounds.items():
        param_grid[name] = np.linspace(bnd[0], bnd[1], num=num_pts_per_dim)
    print(num_pts_per_dim)
    return pd.DataFrame(list(ParameterGrid(param_grid)))

grid_samples = get_grid_samples(bounds, num_samples=num_samples)
grid_samples

3


x1   x2
0  0.0  0.0
1  0.0  0.5
2  0.0  1.0
3  0.5  0.0
4  0.5  0.5
5  0.5  1.0
6  1.0  0.0
7  1.0  0.5
8  1.0  1.0

In [12]:
grid_fig = px.scatter(grid_samples, x="x1", y="x2", width=400, height=400)
grid_fig

### Random Samples

In [13]:
from numpy.random import default_rng

def get_random_samples(bounds, num_samples=9, seed=None):
    rng = default_rng(seed)
    samples = {}
    for parameter, bound in bounds.items():
        samples[parameter] = rng.uniform(bound[0], bound[1], num_samples)
    return pd.DataFrame(samples)

random_samples = get_random_samples(bounds, seed=0)
random_samples

x1        x2
0  0.636962  0.935072
1  0.269787  0.815854
2  0.040974  0.002739
3  0.016528  0.857404
4  0.813270  0.033586
5  0.912756  0.729655
6  0.606636  0.175656
7  0.729497  0.863179
8  0.543625  0.541461

In [14]:
random_fig = px.scatter(random_samples, x="x1", y="x2", width=400, height=400)
random_fig

### Latin Hypercube Samples

In [15]:
def get_latin_hypercube_samples(bounds, num_samples=10, seed=None):
    sampler = qmc.LatinHypercube(d=len(bounds), optimization="random-cd", seed=seed)
    samples = sampler.random(num_samples)
    l_bounds = [bound[0] for bound in bounds.values()]
    u_bounds = [bound[1] for bound in bounds.values()]
    samples = qmc.scale(samples, l_bounds, u_bounds)
    return pd.DataFrame(samples, columns=list(bounds.keys()))

latin_hypercube_samples = get_latin_hypercube_samples(bounds, seed=0)
latin_hypercube_samples

x1        x2
0  0.245638  0.173021
1  0.436304  0.298347
2  0.927034  0.708724
3  0.114260  0.827050
4  0.718673  0.006493
5  0.013682  0.499726
6  0.595903  0.996641
7  0.639336  0.582434
8  0.318415  0.645854
9  0.870029  0.357731

In [16]:
latin_hypercube_fig = px.scatter(
    latin_hypercube_samples, x="x1", y="x2", width=400, height=400
)
latin_hypercube_fig


### Sobol Samples

In [17]:
from scipy.stats.qmc import Sobol

def get_sobol_samples(bounds, num_samples=10, seed=None):
    sampler = Sobol(len(bounds), seed=seed)
    samples = sampler.random(num_samples)
    
    l_bounds = [bound[0] for bound in bounds.values()]
    u_bounds = [bound[1] for bound in bounds.values()]
    samples = qmc.scale(samples, l_bounds, u_bounds)
    
    return pd.DataFrame(samples, columns=list(bounds.keys()))

sobol_samples = get_sobol_samples(bounds, num_samples=num_samples, seed=0)
sobol_samples

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



x1        x2
0  0.850585  0.931366
1  0.451565  0.166937
2  0.248736  0.591645
3  0.584153  0.326728
4  0.663688  0.711389
5  0.014668  0.448486
6  0.312342  0.808678
7  0.897760  0.046263
8  0.987552  0.509826
9  0.339692  0.274682

In [18]:
sobol_fig = px.scatter(sobol_samples, x="x1", y="x2", width=400, height=400)
sobol_fig

### Comparison between sampling methods

In [19]:
sampling_fns = dict(
    grid=get_grid_samples,
    random=get_random_samples,
    latin_hypercube=get_latin_hypercube_samples,
    sobol=get_sobol_samples,
)

sample_nums = [5, 10, 50, 100]
sample_nums.reverse()
        
sample_dfs = []
for name, sampling_fn in sampling_fns.items():
    for num_samples in sample_nums:
        sample_df = sampling_fn(bounds, num_samples)
        sample_df["name"] = name
        sample_df["num_samples"] = num_samples
        sample_dfs.append(sample_df)

compare_df = pd.concat(sample_dfs, axis=0)

10
7
3
2


C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



In [20]:
compare_df

x1        x2   name  num_samples
0   0.000000  0.000000   grid          100
1   0.000000  0.111111   grid          100
2   0.000000  0.222222   grid          100
3   0.000000  0.333333   grid          100
4   0.000000  0.444444   grid          100
..       ...       ...    ...          ...
0   0.698698  0.508323  sobol            5
1   0.410175  0.119933  sobol            5
2   0.240047  0.925973  sobol            5
3   0.901110  0.443818  sobol            5
4   0.808590  0.816340  sobol            5

[657 rows x 4 columns]

In [21]:
fig = px.scatter(
    compare_df,
    x="x1",
    y="x2",
    facet_row="num_samples",
    facet_col="name",
    width=800,
    height=800,
)
plot_and_save(
    "traditional-doe-compare",
    fig,
    show=True,
    mpl_kwargs=dict(width_inches=7.5, height_inches=8.0),
)


### Worsening performance in higher dimensions

In [22]:
one = get_grid_samples(dict(x1=bounds["x1"]), num_samples=3**1)
two = get_grid_samples(dict(x1=bounds["x1"], x2=bounds["x2"]), num_samples=3**2)
three = get_grid_samples(
    dict(x1=bounds["x1"], x2=bounds["x2"], x3=[0.0, 1.0]), num_samples=3**3
)


3
3
3


In [23]:
# https://community.plotly.com/t/plotting-a-simple-1d-number-line/39169/4
import plotly.graph_objects as go
fig = go.Figure()
x = one["x1"]
fig.add_trace(go.Scatter(
    x=x, y=[0] * len(x), mode='markers', marker_size=20,
))
fig.update_xaxes(showgrid=False)
fig.update_yaxes(showgrid=False, 
                 zeroline=True, zerolinecolor='black', zerolinewidth=3,
                 showticklabels=False)
fig.update_layout(height=200, plot_bgcolor='white')
fig.show()

# px.scatter(one, x="x1", y=[0]*3)

In [24]:
px.scatter(two, x="x1", y="x2", width=400, height=400)

In [25]:
# https://community.plotly.com/t/rotating-3d-plots-with-plotly/34776/2
# https://community.plotly.com/t/how-to-export-animation-and-save-it-in-a-video-format-like-mp4-mpeg-or/64621/2
import plotly.graph_objects as go
import numpy as np
import plotly.io as pio

x, y, z = three["x1"], three["x2"], three["x3"]

fig= go.Figure(go.Scatter3d(x=x, y=y, z=z, mode='markers'))

x_eye = -1.25
y_eye = 2
z_eye = 1.0

fig.update_layout(
         title='Animation Test',
         width=600,
         height=600,
         scene_camera_eye=dict(x=x_eye, y=y_eye, z=z_eye),
         updatemenus=[dict(type='buttons',
                  showactive=False,
                  y=1,
                  x=0.8,
                  xanchor='left',
                  yanchor='bottom',
                  pad=dict(t=45, r=10),
                  buttons=[dict(label='Play',
                                 method='animate',
                                 args=[None, dict(frame=dict(duration=5, redraw=True), 
                                                             transition=dict(duration=0),
                                                             fromcurrent=True,
                                                             mode='immediate'
                                                            )]
                                            )
                                      ]
                              )
                        ]
)


def rotate_z(x, y, z, theta):
    w = x+1j*y
    return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

frames=[]
pil_frames = []
for t in np.arange(0, 3.14, 0.025):
    xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
    frames.append(go.Frame(layout=dict(scene_camera_eye=dict(x=xe, y=ye, z=ze))))
fig.frames=frames

fig.show()

In [26]:
[qmc.discrepancy(df.values) for df in [one, two, three]]

[0.0277777777777779, 0.060956790123456894, 0.10033007544581585]

In [27]:
discrepancies = []
for name, sampling_fn in sampling_fns.items():
    for num_samples in sample_nums:
        sample_df = compare_df.query("name == @name and num_samples == @num_samples")
        discrepancies.append(
            dict(
                name=name,
                num_samples=num_samples,
                discrepancy=qmc.discrepancy(sample_df[["x1", "x2"]].values),
            )
        )
        
discrepancy_df = pd.DataFrame(discrepancies)
discrepancy_df

name  num_samples  discrepancy
0              grid          100     0.004093
1              grid           50     0.008708
2              grid           10     0.060957
3              grid            5     0.204861
4            random          100     0.010749
5            random           50     0.008573
6            random           10     0.022572
7            random            5     0.047260
8   latin_hypercube          100     0.000065
9   latin_hypercube           50     0.000220
10  latin_hypercube           10     0.005207
11  latin_hypercube            5     0.018500
12            sobol          100     0.000138
13            sobol           50     0.000390
14            sobol           10     0.008067
15            sobol            5     0.035438

In [28]:
fig = px.scatter(
    compare_df,
    x="x1",
    y="x2",
    facet_row="num_samples",
    facet_col="name",
    width=800,
    height=800,
)

for col, (name, sampling_fn) in enumerate(sampling_fns.items()):
    col = col+1
    for row, num_samples in enumerate(sample_nums):
        row = 4 - row
        fig.add_annotation(
            xref="x domain",
            yref="y domain",
            x=0.5,
            y=-0.1,
            text=f' Discrepancy = {discrepancy_df.query("name == @name and num_samples == @num_samples").iloc[0]["discrepancy"]:.3g} ',
            # text = f"row={row}, col={col}",
            showarrow=False,
            bgcolor="white",
            row=row,
            col=col,
        )

fig_path = "traditional-doe-compare-discrepancy"
fig.update_layout(
    margin=dict(r=40, t=30, b=30),
)
fig.write_html(fig_path + ".html")
fig.write_image(fig_path + ".png")
fig.show()


In [29]:
dim_discrepancies = []
# sample_dfs = []
dim_nums = [2, 3, 10, 20]
num_samples = 100
for name, sampling_fn in sampling_fns.items():
    for num_dims in dim_nums:
        bounds = {f"x{i+1}": [0, 1] for i in range(num_dims)}
        sample_df = sampling_fn(bounds, num_samples, seed=0)
        discrepancy = qmc.discrepancy(sample_df.values)
        dim_discrepancies.append(dict(name=name, num_samples=sample_df.shape[0], discrepancy=discrepancy, num_dims=num_dims))
        # sample_dfs.append(sample_df)

dim_discrepancy_df = pd.DataFrame(dim_discrepancies)
pd.pivot_table(
    dim_discrepancy_df.drop("num_samples", axis=1),
    index=["num_dims", "discrepancy", "name"],
)


10
4
1
1


C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



Empty DataFrame
Columns: []
Index: [(2, 6.409265931739405e-05, latin_hypercube), (2, 0.00013419647223589237, sobol), (2, 0.004092935528052344, grid), (2, 0.006477791186335402, random), (3, 0.0002103949356229151, latin_hypercube), (3, 0.0003235892122264161, sobol), (3, 0.010809351752242069, random), (3, 0.05335594564475454, grid), (10, 0.018653897714654644, latin_hypercube), (10, 0.022224334095691134, sobol), (10, 0.06842806743129515, random), (10, 53.396888619801956, grid), (20, 0.45423472936956166, latin_hypercube), (20, 0.5717774649791076, sobol), (20, 0.8405888642021928, random), (20, 3309.1238072763103, grid)]

In [30]:
dim_discrepancies = []
# sample_dfs = []
dim_nums = [2, 3, 10, 20]
num_samples = 10
for name, sampling_fn in sampling_fns.items():
    for num_dims in dim_nums:
        bounds = {f"x{i+1}": [0, 1] for i in range(num_dims)}
        sample_df = sampling_fn(bounds, num_samples, seed=0)
        discrepancy = qmc.discrepancy(sample_df.values)
        dim_discrepancies.append(dict(name=name, num_samples=sample_df.shape[0], discrepancy=discrepancy, num_dims=num_dims))
        # sample_dfs.append(sample_df)

dim_discrepancy_df = pd.DataFrame(dim_discrepancies)
pd.pivot_table(
    dim_discrepancy_df.drop("num_samples", axis=1),
    index=["num_dims", "discrepancy", "name"],
)


3
2
1
1


C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



Empty DataFrame
Columns: []
Index: [(2, 0.005236766705729812, latin_hypercube), (2, 0.0076472324046004125, sobol), (2, 0.019627671148842563, random), (2, 0.060956790123456894, grid), (3, 0.011434040866014517, latin_hypercube), (3, 0.01451538370993033, sobol), (3, 0.04586154399146114, random), (3, 0.37688078703703676, grid), (10, 0.30414326400414193, latin_hypercube), (10, 0.43743273730096544, sobol), (10, 0.9976404884270602, random), (10, 53.396888619801956, grid), (20, 6.131461128328029, latin_hypercube), (20, 7.369505984936929, sobol), (20, 11.771547486969345, random), (20, 3309.1238072763103, grid)]

In [31]:
dim_discrepancies = []
# sample_dfs = []
dim_nums = [2, 3, 10, 20]
num_samples = 1000
for name, sampling_fn in sampling_fns.items():
    for num_dims in dim_nums:
        bounds = {f"x{i+1}": [0, 1] for i in range(num_dims)}
        sample_df = sampling_fn(bounds, num_samples, seed=0)
        discrepancy = qmc.discrepancy(sample_df.values)
        dim_discrepancies.append(dict(name=name, num_samples=sample_df.shape[0], discrepancy=discrepancy, num_dims=num_dims))
        # sample_dfs.append(sample_df)

dim_discrepancy_df = pd.DataFrame(dim_discrepancies)
pd.pivot_table(
    dim_discrepancy_df.drop("num_samples", axis=1),
    index=["num_dims", "discrepancy", "name"],
)


31
9
1
1


C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



Empty DataFrame
Columns: []
Index: [(2, 1.3837207570865928e-06, latin_hypercube), (2, 1.6838481025072127e-06, sobol), (2, 0.0003923703424881797, grid), (2, 0.001073323450584196, random), (3, 4.8907254588392846e-06, sobol), (3, 8.754559247092786e-06, latin_hypercube), (3, 0.0013353502970596676, random), (3, 0.008351056258295353, grid), (10, 0.0008654031158545905, sobol), (10, 0.001360454305847636, latin_hypercube), (10, 0.007363398310313407, random), (10, 53.396888619801956, grid), (20, 0.043370026241586146, sobol), (20, 0.04457565812541375, latin_hypercube), (20, 0.07909763543233517, random), (20, 3309.1238072763103, grid)]

## Informed Sampling via Bayesian Optimization

i.e. an algorithm that uses information about the objective function to be optimized.

### Objective Function
Discrepancy is no longer a satisfactory measure of performance, since we're now moving
to a situation where we can leverage information about the function we're trying to
optimize; however, we still need to decide on an objective function.

We'll start with using an analytic 2D function, called the "Branin function", with a
limited evaluation budget.

In [32]:
from ax.utils.measurement.synthetic_functions import branin
branin(2.0, 3.0)

6.115426298669772

In [33]:
total_trials = 20

Let's peak at the solution space to get an idea of how
complex the function is. Note that there are three global minima in the Branin function.

In [34]:
bounds = {"x1": [-5.0, 10.0], "x2": [0.0, 10.0]}
branin_samples = get_sobol_samples(bounds, num_samples=10000, seed=None)
branin_values = branin(branin_samples.values)
px.scatter(
    branin_samples,
    x="x1",
    y="x2",
    color=branin_values,
    width=400,
    height=400,
    labels=dict(color="branin"),
)


C:\Users\sterg\AppData\Local\Temp\ipykernel_6300\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.



It becomes more obvious where the three minima are if we use logarithmic scaling for the
Branin function values.

In [35]:
fig = px.scatter(
    branin_samples,
    x="x1",
    y="x2",
    color=np.log(branin_values),
    width=400,
    height=400,
    labels=dict(color="log_branin"),
)
fig


Next, we'll perform closed-loop optimization in Meta's Adaptive Experimentation (Ax)
platform using their simplest API, the "Loop API" via the `optimize` function.

In [36]:
from ax import optimize

objective_name = "branin"

def evaluate(parameters):
    return {objective_name: branin(parameters["x1"], parameters["x2"])}

best_parameters, values, experiment, model = optimize(
    parameters=[
        {
            "name": "x1",
            "type": "range",
            "bounds": [-5.0, 10.0],
        },
        {
            "name": "x2",
            "type": "range",
            "bounds": [0.0, 10.0],
        },
    ],
    evaluation_function=evaluate,
    objective_name = objective_name,
    minimize=True,
    total_trials=total_trials,
    random_seed=0,
)

[INFO 11-15 22:34:07] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x1. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 22:34:07] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x2. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 22:34:07] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x1', parameter_type=FLOAT, range=[-5.0, 10.0]), RangeParameter(name='x2', parameter_type=FLOAT, range=[0.0, 10.0])], parameter_constraints=[]).
[INFO 11-15 22:34:07] ax.modelbridge.dispatch_utils: Using Bayesian optimization since there are more ordered parameters than there are categories for the unordered categorical parameters.
[INFO 11-15 22:34:07] ax.modelbridge.dispatch_utils:

Let's take a look at how well we did in optimizing the function.

In [37]:
print(best_parameters, values[0])

{'x1': 3.215144226430965, 'x2': 2.3153385771007335} {'branin': 0.4212055370817325}


In [38]:
fig.add_trace(
    go.Scatter(
        x=[best_parameters["x1"]],
        y=[best_parameters["x2"]],
        mode="markers",
        marker=dict(
            color="red",
            size=10,
        ),
    )
)
d = fig.to_dict()
d["data"][0]["type"] = "scatter"
fig2 = go.Figure(d)
fig2.update_layout(showlegend=False)
fig2


Looks like Bayesian optimization did a pretty good job at finding one of the global
minima in a limited number of evaluations. We can also have a look at the actual
"experiments" that were performed, as well as the model predictions (mean and uncertainty).

In [39]:
from ax.plot.contour import plot_contour
from ax.utils.notebook.plotting import render, init_notebook_plotting
init_notebook_plotting()
render(plot_contour(model, "x1", "x2", metric_name=objective_name))

[INFO 11-15 22:34:16] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


## Comparison between sampling methods

To make a fair comparison between methods, it's best if we can look at average behavior
across multiple repeat runs, or "campaigns".

### Helper Functions

Since the Bayesian Optimization API is
different from the functions we've defined previously, we'll create a function for
extracting the parameters and their objective values.

In [41]:
def extract_data(experiment):
    trials = experiment.trials
    params = [experiment.trials[key].arm.parameters for key in trials.keys()]
    bayes_df = pd.DataFrame(params)
    bayes_df["objective"] = experiment.fetch_data().df["mean"]
    return bayes_df

bayes_df = extract_data(experiment)
bayes_df

x1         x2  objective
0    2.126608   5.925240  12.362557
1    3.681450   0.371219   4.075152
2    9.260048   8.623440  40.015122
3   -3.193132   2.614422  96.152604
4   -1.775822   9.741822   8.303279
5    7.059405   1.815269  17.227185
6    2.114085  10.000000  51.103584
7    4.201676   3.440811   8.719202
8   -4.994582  10.000000  64.107713
9    2.339113   2.539417   3.524907
10  10.000000   0.000000  10.960889
11  10.000000   3.181537   1.975032
12   2.152317   0.000000  14.793055
13   3.215144   2.315339   0.433257
14  -0.370447   7.619329  19.974938
15   9.246282   2.463945   0.568778
16   9.037910   3.845225   3.920599
17   2.917731   3.421616   1.569793
18   9.586286   2.546111   0.527542
19   3.100630   1.856731   0.608831

For visualization purposes, it will also help to visualize the best objective so far as
a function of the iteration number.

In [42]:
def add_best_obj_so_far(df):
    df["iteration"] = range(1, len(df) + 1)
    df["best_obj"] = df["objective"].cummin()
    return df

bayes_df = add_best_obj_so_far(bayes_df)
bayes_df

x1         x2  objective  iteration   best_obj
0    2.126608   5.925240  12.362557          1  12.362557
1    3.681450   0.371219   4.075152          2   4.075152
2    9.260048   8.623440  40.015122          3   4.075152
3   -3.193132   2.614422  96.152604          4   4.075152
4   -1.775822   9.741822   8.303279          5   4.075152
5    7.059405   1.815269  17.227185          6   4.075152
6    2.114085  10.000000  51.103584          7   4.075152
7    4.201676   3.440811   8.719202          8   4.075152
8   -4.994582  10.000000  64.107713          9   4.075152
9    2.339113   2.539417   3.524907         10   3.524907
10  10.000000   0.000000  10.960889         11   3.524907
11  10.000000   3.181537   1.975032         12   1.975032
12   2.152317   0.000000  14.793055         13   1.975032
13   3.215144   2.315339   0.433257         14   0.433257
14  -0.370447   7.619329  19.974938         15   0.433257
15   9.246282   2.463945   0.568778         16   0.433257
16   9.037910   3.845225   3.920599         17   0.433257
17   2.917731   3.421616   1.569793         18   0.433257
18   9.586286   2.546111   0.527542         19   0.433257
19   3.100630   1.856731   0.608831         20   0.433257

In [43]:
px.line(bayes_df, x="iteration", y="best_obj")

### Bayesian Campaigns

We'll add some jitter to the bounds of the objective function so that when we compare
with methods that tend to do systematic sampling (in particular, grid search), we are
making a fair comparison.

In [44]:
def get_noisy_bounds(bounds, seed=None, noise_scale=2):
    rng = default_rng(seed)
    return {
        key: np.add(bound, rng.uniform(-1 * noise_scale, noise_scale, 2)).tolist()
        for key, bound in bounds.items()
    }
    
get_noisy_bounds(bounds, seed=0)

{'x1': [-4.452153250714183, 9.07914685505548],
 'x2': [-1.8361059042552212, 8.066110542114117]}

In [45]:
num_repeats = 50
SEEDS = list(range(num_repeats))
bayes_results = []
for seed in SEEDS:
    noisy_bounds = get_noisy_bounds(bounds, seed=seed)
    results = optimize(
        parameters=[
            {
                "name": "x1",
                "type": "range",
                "bounds": noisy_bounds["x1"],
            },
            {
                "name": "x2",
                "type": "range",
                "bounds": noisy_bounds["x2"],
            },
        ],
        evaluation_function=evaluate,
        objective_name=objective_name,
        minimize=True,
        total_trials=total_trials,
        random_seed=seed,
    )
    
    bayes_results.append(
        dict(
            best_parameters=results[0],
            values=results[1],
            experiment=results[2],
            model=results[3],
        )
    )

[INFO 11-15 22:39:02] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x1. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 22:39:02] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x2. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 22:39:02] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x1', parameter_type=FLOAT, range=[-4.452153250714183, 9.07914685505548]), RangeParameter(name='x2', parameter_type=FLOAT, range=[-1.8361059042552212, 8.066110542114117])], parameter_constraints=[]).
[INFO 11-15 22:39:02] ax.modelbridge.dispatch_utils: Using Bayesian optimization since there are more ordered parameters than there are categories for the unordered categorical parameter

KeyboardInterrupt: 

In [257]:
bayes_results_df = pd.DataFrame(bayes_results)
bayes_results_df

best_parameters  \
0   {'x1': 3.062282886183861, 'x2': 2.290498757345...   
1   {'x1': 2.885064009169117, 'x2': 2.469607469883...   
2   {'x1': 3.1059336313274404, 'x2': 2.32686199951...   
3   {'x1': 3.192649591907619, 'x2': 2.252360843789...   
4   {'x1': 9.476454875247152, 'x2': 2.398544191523...   
5   {'x1': 9.240225310662296, 'x2': 2.370824085180...   
6   {'x1': 9.373083479253353, 'x2': 2.428146615822...   
7   {'x1': 3.186233058293193, 'x2': 2.127644670305...   
8   {'x1': 3.2634594548024136, 'x2': 2.37895736068...   
9   {'x1': 3.348510046172086, 'x2': 2.050021325757...   
10  {'x1': 3.1400109093949164, 'x2': 2.26628402206...   
11  {'x1': 9.439011200579953, 'x2': 2.685681499003...   
12  {'x1': 9.396780128730665, 'x2': 2.510946583878...   
13  {'x1': 9.444955819898738, 'x2': 2.527359528742...   
14  {'x1': 9.443786667337026, 'x2': 2.260346348517...   
15  {'x1': 3.2271932479967687, 'x2': 2.54775142293...   
16  {'x1': 9.473303191131839, 'x2': 2.594258264139...   
17  {'x1': 3.0787301024081875, 'x2': 2.41661384669...   
18  {'x1': 3.2522023147476027, 'x2': 2.29429599731...   
19  {'x1': 9.515907242207646, 'x2': 2.563941678150...   
20  {'x1': 3.2331144741924636, 'x2': 1.98423528499...   
21  {'x1': 3.1550899336451814, 'x2': 2.51422803232...   
22  {'x1': 3.202414896186731, 'x2': 2.023359085171...   
23  {'x1': 9.553799908018837, 'x2': 2.851665089796...   
24  {'x1': 9.620709262556575, 'x2': 2.729189600706...   
25  {'x1': 3.148681497625099, 'x2': 2.400408505650...   
26  {'x1': 3.025135804870298, 'x2': 2.319923183570...   
27  {'x1': 3.092156271937661, 'x2': 2.50537219145075}   
28  {'x1': 3.1239317880151254, 'x2': 2.03787980676...   
29  {'x1': 9.490257768531286, 'x2': 2.511791651841...   
30  {'x1': 9.716427994663245, 'x2': 2.68759046604037}   
31  {'x1': 3.146061555913755, 'x2': 2.511330714857...   
32  {'x1': 3.02647342214778, 'x2': 2.3283091957156...   
33  {'x1': 3.3428442638530464, 'x2': 1.63241509984...   
34  {'x1': 3.2044190069986467, 'x2': 2.48025867008...   
35  {'x1': -3.068897507505538, 'x2': 11.7873027829...   
36  {'x1': 3.024157134727723, 'x2': 2.347229650912...   
37  {'x1': 9.425801304913808, 'x2': 2.496360631395...   
38  {'x1': 3.2096108672854244, 'x2': 2.09057122494...   
39  {'x1': 3.1800001246674334, 'x2': 2.37954248301...   
40  {'x1': 3.168194367159799, 'x2': 2.300845579527...   
41  {'x1': 9.332215368201858, 'x2': 2.501486621153...   
42  {'x1': 3.1352255927352806, 'x2': 2.19924922193...   
43  {'x1': 3.085310565727511, 'x2': 2.091913022180...   
44  {'x1': 3.4116840636394725, 'x2': 2.35033900272...   
45  {'x1': 9.58941067290702, 'x2': 2.5909199846319...   
46  {'x1': 3.122075288454485, 'x2': 2.271011284577...   
47  {'x1': 9.427078043816897, 'x2': 2.489567018928...   
48  {'x1': 3.0233611185448304, 'x2': 2.71941697161...   
49  {'x1': 3.2078753136848075, 'x2': 1.81576067739...   

                                               values        experiment  \
0   ({'branin': 0.42501440426879356}, {'branin': {...  Experiment(None)   
1   ({'branin': 0.7411746982689031}, {'branin': {'...  Experiment(None)   
2   ({'branin': 0.4227229370765464}, {'branin': {'...  Experiment(None)   
3   ({'branin': 0.40162237898055864}, {'branin': {...  Experiment(None)   
4   ({'branin': 0.44678791865119294}, {'branin': {...  Experiment(None)   
5   ({'branin': 0.5743912528013801}, {'branin': {'...  Experiment(None)   
6   ({'branin': 0.3702381106448076}, {'branin': {'...  Experiment(None)   
7   ({'branin': 0.4346880415287657}, {'branin': {'...  Experiment(None)   
8   ({'branin': 0.51800874020946}, {'branin': {'br...  Experiment(None)   
9   ({'branin': 0.5849916316123149}, {'branin': {'...  Experiment(None)   
10  ({'branin': 0.3946472338727496}, {'branin': {'...  Experiment(None)   
11  ({'branin': 0.4633717622309028}, {'branin': {'...  Experiment(None)   
12  ({'branin': 0.4198746562478384}, {'branin': {'...  Experiment(None)   
13  ({'branin': 0.4075506156143458}, {'branin': {'...  Experiment(None)   
14  (

In [258]:
bayes_dfs = [
    add_best_obj_so_far(extract_data(result["experiment"])) for result in bayes_results
]
bayes_dfs[0]

x1        x2   objective  iteration  best_obj
0   1.976665  4.031195    6.661052          1  6.661052
1   3.379267 -1.468516   13.380335          2  6.661052
2   8.411646  6.703012   29.421102          3  6.661052
3  -2.822202  0.752751  116.830170          4  6.661052
4  -1.543665  7.810457   11.170977          5  6.661052
5   2.719343  7.692859   26.900846          6  6.661052
6   5.516253  2.008512   17.648279          7  6.661052
7   7.472312 -1.836106   23.540793          8  6.661052
8  -4.452153  8.066111   64.991214          9  6.661052
9   0.149044  8.066111   24.787739         10  6.661052
10  3.316180  2.083265    0.547398         11  0.547398
11  3.713832  4.186351    7.288275         12  0.547398
12  2.388035  1.615070    4.742496         13  0.547398
13  9.079147  1.601440    1.322680         14  0.547398
14  9.079147 -0.673326    9.215337         15  0.547398
15  2.890503  2.927276    0.899977         16  0.547398
16  9.079147  3.068220    1.721481         17  0.547398
17  8.377015  2.319371    5.547465         18  0.547398
18  3.062283  2.290499    0.430295         19  0.430295
19  3.217619  2.557852    0.542174         20  0.430295

Now that we've performed repeat campaigns for Bayesian optimization, we can take a look
at the average behavior across the campaigns.

In [259]:
from self_driving_lab_demo.utils.plotting import line

bayes_best_objs = [bayes_df["best_obj"] for bayes_df in bayes_dfs]
bayes_mean = np.mean(bayes_best_objs, axis=0)
bayes_std = np.std(bayes_best_objs, axis=0)

bayes_line_df = pd.DataFrame(dict(iteration=bayes_dfs[0]["iteration"], mean=bayes_mean, std=bayes_std))
bayes_line_df["name"] = "bayes"

line(data_frame=bayes_line_df, x="iteration", y="mean", error_y="std", error_y_mode="band", range_y=[0, 60])

Now that we have our Bayesian optimization results, we can compute and compare with the
other search types.

In [260]:
from numpy.random import default_rng

rng = default_rng(0)
sample_dfs = []
for name, sampling_fn in sampling_fns.items():
    for seed in SEEDS:
        noisy_bounds = get_noisy_bounds(bounds, rng)
        sample_df = sampling_fn(
            noisy_bounds, num_samples=total_trials, seed=seed
        ).sample(frac=1.0)
        sample_df["name"] = name
        sample_df["total_trials"] = total_trials
        sample_df["seed"] = seed
        sample_df["iteration"] = range(1, len(sample_df) + 1)
        sample_dfs.append(sample_df)


4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4
4


C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\2746881076.py:5: UserWarning:

The balance pr

In [261]:
doe_df = pd.concat(sample_dfs, axis=0)
doe_df["objective"] = branin(doe_df[["x1", "x2"]].values)
doe_df

x1        x2   name  total_trials  seed  iteration  objective
12  9.079147 -1.836106   grid            20     0          1  17.246893
4   0.058280 -1.836106   grid            20     0          2  79.552078
7   0.058280  8.066111   grid            20     0          3  24.244619
9   4.568713  1.464633   grid            20     0          4   8.626712
11  4.568713  8.066111   grid            20     0          5  52.727465
..       ...       ...    ...           ...   ...        ...        ...
10  0.857527  2.150423  sobol            20    49         16  22.937999
3   9.463492  9.350751  sobol            20    49         17  47.230385
11  7.040043  7.480518  sobol            20    49         18  56.449575
8   3.361274  3.124848  sobol            20    49         19   1.658748
9  -2.327759  9.947245  sobol            20    49         20   3.615356

[3800 rows x 7 columns]

In [262]:
name = "grid"
doe_df.query("name == @name and total_trials == @total_trials")

x1        x2  name  total_trials  seed  iteration   objective
12   9.079147 -1.836106  grid            20     0          1   17.246893
4    0.058280 -1.836106  grid            20     0          2   79.552078
7    0.058280  8.066111  grid            20     0          3   24.244619
9    4.568713  1.464633  grid            20     0          4    8.626712
11   4.568713  8.066111  grid            20     0          5   52.727465
..        ...       ...   ...           ...   ...        ...         ...
14  11.090597  7.544008  grid            20    49         12   21.836537
1   -6.974364  4.728535  grid            20    49         13  365.417567
13  11.090597  4.728535  grid            20    49         14   11.151047
2   -6.974364  7.544008  grid            20    49         15  268.297642
6   -0.952711  7.544008  grid            20    49         16   15.572210

[800 rows x 7 columns]

In [263]:
sub_dfs = []
for name, sampling_fn in sampling_fns.items():
    for seed in range(num_repeats):
        sub_df = doe_df.query(
            "name == @name and total_trials == @total_trials and seed == @seed",
        )
        sub_df.loc[:, "best_obj"] = sub_df["objective"].cummin()
        sub_dfs.append(sub_df)

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\1933624879.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\1933624879.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\sterg\AppData\Local\Temp\ipykernel_2824\1933624879.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

In [264]:
doe_best_df = pd.concat(sub_dfs, axis=0)
grp = doe_best_df.groupby(["name", "total_trials", "iteration"], as_index=False)
doe_result_df = grp.mean().drop("seed", axis=1)
doe_result_df = doe_result_df.rename(columns=dict(best_obj="mean"))
doe_result_df.loc[:, "std"] = grp.std()["best_obj"]

In [265]:
doe_result_df

name  total_trials  iteration        x1        x2  objective       mean  \
0    grid            20          1  2.935935  5.418857  62.240871  62.240871   
1    grid            20          2  2.993028  5.560262  68.921441  35.783386   
2    grid            20          3  3.277358  4.968909  67.076228  18.088278   
3    grid            20          4  2.026970  4.182076  67.747197  14.875737   
4    grid            20          5  2.572302  4.868641  91.613445  13.192362   
..    ...           ...        ...       ...       ...        ...        ...   
71  sobol            20         16  2.167826  5.299904  30.175658   3.847949   
72  sobol            20         17  2.356251  5.284081  47.665191   3.619995   
73  sobol            20         18  2.575264  5.202705  48.575340   3.619995   
74  sobol            20         19  1.676074  5.082647  46.298847   3.268283   
75  sobol            20         20  2.937136  5.088483  43.598242   3.121778   

          std  
0   65.343231  
1   43.968446  
2   13.084918  
3   10.989903  
4    9.403302  
..        ...  
71   2.509028  
72   2.474527  
73   2.474527  
74   2.079658  
75   1.988530  

[76 rows x 8 columns]

In [266]:
line_df = pd.concat([bayes_line_df, doe_result_df[["name", "iteration", "mean", "std"]]])
line_df

iteration       mean        std   name
0           1  52.210913  66.523704  bayes
1           2  25.569411  19.484752  bayes
2           3  13.806625   9.609292  bayes
3           4  11.142287   6.591441  bayes
4           5   9.307427   6.159751  bayes
..        ...        ...        ...    ...
71         16   3.847949   2.509028  sobol
72         17   3.619995   2.474527  sobol
73         18   3.619995   2.474527  sobol
74         19   3.268283   2.079658  sobol
75         20   3.121778   1.988530  sobol

[96 rows x 4 columns]

In [267]:
fig = line(
    data_frame=line_df,
    x="iteration",
    y="mean",
    error_y="std",
    color="name",
    error_y_mode="band",
    range_y=[0, 30],
    labels=dict(mean="branin function value")
)
fig.update_layout(hovermode="x")
fig

## Higher Dimensions

We observed trends in the 2D case, but what about higher dimensions? Let's try a 6D
example. Since we can't easily visualize the full solution space in advance, instead
we'll provide the analytic formula here as well as a description of the function. The
Hartmann6 function is a 6D function with 6 local minima, in contrast to the Branin
function which was 2D and had 3 global minima. The function is [defined](https://www.sfu.ca/~ssurjano/hart6.html) as follows:

$f(\mathbf{x})=-\sum_{i=1}^4 \alpha_i \exp \left(-\sum_{j=1}^6 A_{i j}\left(x_j-P_{i
j}\right)^2\right)$, where

$\alpha=(1.0,1.2,3.0,3.2)^T$

$\mathbf{A}=\left(\begin{array}{cccccc}10 & 3 & 17 & 3.50 & 1.7 & 8 \\ 0.05 & 10 & 17 & 0.1 & 8 & 14 \\ 3 & 3.5 & 1.7 & 10 & 17 & 8 \\ 17 & 8 & 0.05 & 10 & 0.1 & 14\end{array}\right)$

$\mathbf{P}=10^{-4}\left(\begin{array}{cccccc}1312 & 1696 & 5569 & 124 & 8283 & 5886 \\
2329 & 4135 & 8307 & 3736 & 1004 & 9991 \\ 2348 & 1451 & 3522 & 2883 & 3047 & 6650 \\
4047 & 8828 & 8732 & 5743 & 1091 & 381\end{array}\right)$

The inputs are $x_j, j \in {1,2,3,4,5,6}$ which are typically in the bounds of $[0,1]$.

Finally, the global minimum is given by:

$f\left(\mathbf{x}^*\right)=-3.32237$, at
$\mathbf{x}^*=(0.20169,0.150011,0.476874,0.275332,0.311652,0.6573)$

Compared with the previous experiment, we'll also allow for more total trials while
keeping in mind that materials optimization tasks are typically both high-dimensional
and subject to a limited number of evaluations.

In [2]:
from ax.utils.measurement.synthetic_functions import hartmann6
from ax import optimize


total_trials = 50
objective_name = "hartmann6"


def evaluate(parameters):
    return {
        objective_name: hartmann6(
            parameters["x1"],
            parameters["x2"],
            parameters["x3"],
            parameters["x4"],
            parameters["x5"],
            parameters["x6"],
        )
    }


best_parameters, values, experiment, model = optimize(
    parameters=[
        {
            "name": "x1",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
        {
            "name": "x2",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
        {
            "name": "x3",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
        {
            "name": "x4",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
        {
            "name": "x5",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
        {
            "name": "x6",
            "type": "range",
            "bounds": [0.0, 1.0],
        },
    ],
    evaluation_function=evaluate,
    objective_name=objective_name,
    minimize=True,
    total_trials=total_trials,
    random_seed=0,
)


[INFO 11-15 17:08:34] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x1. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 17:08:34] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x2. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 17:08:34] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x3. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 17:08:34] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x4. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 

In [46]:
num_repeats = 50
SEEDS = list(range(num_repeats))

bounds = {
    "x1": [0, 1],
    "x2": [0, 1],
    "x3": [0, 1],
    "x4": [0, 1],
    "x5": [0, 1],
    "x6": [0, 1],
}

bayes_results = []
for seed in SEEDS:
    noisy_bounds = get_noisy_bounds(bounds, seed=seed)
    results = optimize(
        parameters=[
            {
                "name": "x1",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
            {
                "name": "x2",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
            {
                "name": "x3",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
            {
                "name": "x4",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
            {
                "name": "x5",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
            {
                "name": "x6",
                "type": "range",
                "bounds": [0.0, 1.0],
            },
        ],
        evaluation_function=evaluate,
        objective_name=objective_name,
        minimize=True,
        total_trials=total_trials,
        random_seed=seed,
    )
    
    bayes_results.append(
        dict(
            best_parameters=results[0],
            values=results[1],
            experiment=results[2],
            model=results[3],
        )
    )
    
bayes_results_df = pd.DataFrame(bayes_results)

[INFO 11-15 18:06:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x1. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 18:06:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x2. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 18:06:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x3. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 18:06:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter x4. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.
[INFO 11-15 

In [47]:
bayes_dfs = [
    add_best_obj_so_far(extract_data(result["experiment"])) for result in bayes_results
]

bayes_best_objs = [bayes_df["best_obj"] for bayes_df in bayes_dfs]
bayes_mean = np.mean(bayes_best_objs, axis=0)
bayes_std = np.std(bayes_best_objs, axis=0)

bayes_line_df = pd.DataFrame(
    dict(iteration=bayes_dfs[0]["iteration"], mean=bayes_mean, std=bayes_std)
)
bayes_line_df["name"] = "bayes"


In [48]:
from numpy.random import default_rng

rng = default_rng(0)
sample_dfs = []
for name, sampling_fn in sampling_fns.items():
    for seed in SEEDS:
        noisy_bounds = get_noisy_bounds(bounds, rng, noise_scale=0.1)
        sample_df = sampling_fn(
            noisy_bounds, num_samples=total_trials, seed=seed
        ).sample(frac=1.0)
        sample_df["name"] = name
        sample_df["total_trials"] = total_trials
        sample_df["seed"] = seed
        sample_df["iteration"] = range(1, len(sample_df) + 1)
        sample_dfs.append(sample_df)

doe_df = pd.concat(sample_dfs, axis=0)
doe_df["objective"] = hartmann6(doe_df[["x1", "x2", "x3", "x4", "x5", "x6"]].values)

sub_dfs = []
for name, sampling_fn in sampling_fns.items():
    for seed in range(num_repeats):
        sub_df = doe_df.query(
            "name == @name and total_trials == @total_trials and seed == @seed",
        )
        sub_df.loc[:, "best_obj"] = sub_df["objective"].cummin()
        sub_dfs.append(sub_df)
        
doe_best_df = pd.concat(sub_dfs, axis=0)
grp = doe_best_df.groupby(["name", "total_trials", "iteration"], as_index=False)
doe_result_df = grp.mean().drop("seed", axis=1)
doe_result_df = doe_result_df.rename(columns=dict(best_obj="mean"))
doe_result_df.loc[:, "std"] = grp.std()["best_obj"]

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The balance properties of Sobol' points require n to be a power of 2.

C:\Users\sterg\AppData\Local\Temp\ipykernel_12628\2746881076.py:5: UserWarning:

The bal

In [49]:
line_df = pd.concat(
    [bayes_line_df, doe_result_df[["name", "iteration", "mean", "std"]]]
)


In [50]:
fig = line(
    data_frame=line_df,
    x="iteration",
    y="mean",
    error_y="std",
    color="name",
    error_y_mode="band",
    # range_y=[0, 30],
    labels=dict(mean="hartmann6 function value")
)
fig.update_layout(margin=dict(r=40, t=30, b=30), hovermode="x")

fig_path = "hartmann6-comparison"
fig.write_html(fig_path + ".html")
fig.write_image(fig_path + ".png")
fig.show()

## Code Graveyard

In [22]:
# from ax.modelbridge.factory import get_sobol
# from ax.service.ax_client import AxClient

# def get_sobol_samples(bounds, num_samples=10):
#     parameters = [
#             {
#                 "name": "x1",
#                 "type": "range",
#                 "bounds": bounds["x1"],
#             },
#             {
#                 "name": "x2",
#                 "type": "range",
#                 "bounds": bounds["x2"],
#             },
#         ]

#     client = AxClient()
#     client.create_experiment(
#         name="experiment",
#         parameters=parameters,  # type: ignore
#     )
        
#     m = get_sobol(client.experiment.search_space)
#     gr = m.gen(n=num_samples)
#     gr

In [23]:
# compare_samples = {}
# for name, sampling_fn in sampling_fns.items():
#     compare_samples[name] = {}
#     for num_samples in sample_nums:
#         compare_samples[name][num_samples] = sampling_fn(bounds, num_samples)
        
# df = pd.DataFrame(compare_samples)
# df.index.name = "num_samples"
# df

In [24]:
# three_plot_df = three.copy()
# three_plot_df["step"] = (np.arange(0, three_plot_df.shape[0]))
# three_plot_df["group"] = 1

# px.scatter_3d(three_plot_df, x="x1", y="x2", z="x3", animation_frame="step", animation_group="group", width=400, height=400)


In [25]:
# discrepancies = []
# for name, sampling_fn in sampling_fns.items():
#     for num_samples in sample_nums:
#         sample_df = compare_df.query("name == @name and num_samples == @num_samples")
#         sample_df["discrepancy"] = qmc.discrepancy(sample_df[["x1", "x2"]].values)
#         sample_dfs.append(sample_df)

# compare_df_2 = pd.concat(sample_dfs, axis=0)
# compare_df_2